In [ ]:
import numpy  # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

from __future__ import print_function
import tensorflow as tf
from six.moves import range
import numpy as np
import os
import sys

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import confusion_matrix,classification_report

from tensorflow.contrib import keras
from keras import models, layers, losses, optimizers, metrics
from keras.models import Sequential
from keras.layers import Dense

# fix random seed for reproducibility
seed = 8
numpy.random.seed(seed)

In [ ]:
df = pd.read_csv('/Users/anamika/Downloads/diabetes.csv')

In [ ]:
df.head()

In [ ]:
# Splitting into training and testing datasets

X = df.drop(['Outcome'], axis=1)
Y = df['Outcome']

X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.3)

In [ ]:
scaler = MinMaxScaler()

scaled_x_train = scaler.fit_transform(X_train)
scaled_x_test = scaler.transform(X_test)

In [ ]:
# Create Keras Model

model = models.Sequential()

# Hyperparameters
hold_prob = 0.01
beta = 1e-8
alpha = 0.05
lr_decay = 0.01
iterations = 400
validation_split = 0.5
opt_momentum = 0.9 # (Use only for SGD)
batch_size = 32

In [ ]:
# Optimizer
opt = optimizers.SGD(lr=alpha, decay=lr_decay, momentum=opt_momentum, nesterov=True)

# First Layer
model.add(layers.Dense(input_dim=8, units=8, activation='relu'))

# Hidden Layers
model.add(layers.Dense(units=8, activation='relu', kernel_regularizer=keras.regularizers.l2(beta)))
model.add(layers.Dropout(hold_prob))

model.add(layers.Dense(units=8, activation='relu', kernel_regularizer=keras.regularizers.l2(beta)))
model.add(layers.Dropout(hold_prob))

model.add(layers.Dense(units=8, activation='relu', kernel_regularizer=keras.regularizers.l2(beta)))
model.add(layers.Dropout(hold_prob))

# Output Layer
model.add(layers.Dense(units=2, activation='softmax'))

# Compiling the Model
model.compile(optimizer=opt, loss='sparse_categorical_crossentropy', metrics=['accuracy'])

# Train
model.fit(x=scaled_x_train, y=y_train, epochs=iterations, validation_split=validation_split, batch_size=batch_size)

In [ ]:
##  check how our model performs on new data

predictions = model.predict_classes(scaled_x_test)
print(classification_report(y_test, predictions))

In [ ]:
## Try to treat missing values and than apply the same algorithm and check the difference in accuracy
## Using matplotlib plot the histogram between each feature and output